Download Dataset: https://drive.google.com/file/d/1tedoFTFFBbM2iUvdg37WQFSq07ghYrll/view?usp=drive_link

### Adding Libraries

In [15]:
import pandas as pd
import os
import math
import numpy as np
import base64
from PIL import Image
import io
import cv2

### Make All The Images

In [4]:
def load_data(filepath):
    """Load CSV data into a DataFrame."""
    return pd.read_csv(filepath)

# load CSV data
data = pd.read_csv('../data/dataset.csv', skiprows=1)

save_path = '../data/image_files/'
if not os.path.exists(save_path):
    os.makedirs(save_path)

# read dataset.csv data {lable, pixcels}
for index, row in data.iterrows():
    label = row.iloc[0]
    pixels = row.iloc[1].split(' ')
    pixels = list(map(int, pixels))
    
    # calculate image real sizes
    image_size = int(math.sqrt(len(pixels)))
    image_array = np.array(pixels, dtype=np.uint8).reshape((image_size, image_size))
    
    # creat image and save
    image = Image.fromarray(image_array)
    image.save(os.path.join(save_path, f'label_{label}_index_{index}.png'))

### Detecting All The Faces

In [5]:
# مسیر پوشه‌ای که تصاویر در آن ذخیره شده‌اند
image_folder_path = '../Data/image_files'

# بارگذاری مدل پیش‌آموزش دیده برای تشخیص چهره
face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + 'haarcascade_frontalface_default.xml')

# تابعی برای تشخیص وضوح چهره در تصویر
def detect_face_and_clarity(image_path):
    image = cv2.imread(image_path)
    gray_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    
    # تشخیص چهره‌ها
    faces = face_cascade.detectMultiScale(gray_image, 1.1, 4)
    
    if len(faces) == 0:
        return 0  # اگر چهره‌ای تشخیص داده نشد، وضوح را 0 درصد در نظر می‌گیریم
    
    # محاسبه مساحت کل تصویر
    total_area = image.shape[0] * image.shape[1]
    
    # محاسبه مساحت کل چهره‌های تشخیص داده شده
    face_area = sum((x2 - x) * (y2 - y) for x, y, x2, y2 in faces)
    
    # محاسبه درصد وضوح چهره بر اساس نسبت مساحت چهره به کل تصویر
    clarity_percentage = (face_area / total_area) * 100
    
    return clarity_percentage

# برای هر تصویر در پوشه، تشخیص وضوح چهره را انجام دهید و یک دیکشنری بسازید
clarity_dict = {}
for image_name in os.listdir(image_folder_path):
    image_path = os.path.join(image_folder_path, image_name)
    clarity_percentage = detect_face_and_clarity(image_path)
    clarity_dict[image_name] = clarity_percentage

# نمایش دیکشنری وضوح چهره
for image_name, clarity in clarity_dict.items():
    print(f"Image: {image_name}, Clarity: {clarity:.2f}%")


Image: label_0_index_0.png, Clarity: 0.00%
Image: label_0_index_10001.png, Clarity: 54.69%
Image: label_0_index_10015.png, Clarity: 0.00%
Image: label_0_index_10036.png, Clarity: 0.00%
Image: label_0_index_10037.png, Clarity: 51.65%
Image: label_0_index_10051.png, Clarity: 18.45%
Image: label_0_index_10056.png, Clarity: 0.00%
Image: label_0_index_10062.png, Clarity: 69.44%
Image: label_0_index_10064.png, Clarity: 0.00%
Image: label_0_index_10068.png, Clarity: 0.00%
Image: label_0_index_10078.png, Clarity: 0.00%
Image: label_0_index_10094.png, Clarity: 0.00%
Image: label_0_index_10099.png, Clarity: 59.42%
Image: label_0_index_10104.png, Clarity: 56.21%
Image: label_0_index_10114.png, Clarity: 0.00%
Image: label_0_index_10120.png, Clarity: 71.18%
Image: label_0_index_10121.png, Clarity: 0.00%
Image: label_0_index_1014.png, Clarity: 0.00%
Image: label_0_index_10141.png, Clarity: 0.00%
Image: label_0_index_10147.png, Clarity: 44.40%
Image: label_0_index_1015.png, Clarity: 0.00%
Image: labe

### Clarify All

In [ ]:
# Define a function to calculate the clarity of an image
def calculate_image_clarity(image_path):
    image = cv2.imread(image_path)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    fm = cv2.Laplacian(gray, cv2.CV_64F).var()
    return fm

# Define a function to check if an image is clear enough
def is_image_clear(image_path, clarity_threshold=100):
    clarity = calculate_image_clarity(image_path)
    return clarity > clarity_threshold

# Define a function to save relevant images to a new path
def save_relevant_images(source_folder, destination_folder, clarity_threshold=100):
    if not os.path.exists(destination_folder):
        os.makedirs(destination_folder)
    
    for image_name in os.listdir(source_folder):
        source_image_path = os.path.join(source_folder, image_name)
        destination_image_path = os.path.join(destination_folder, image_name)
        
        if is_image_clear(source_image_path, clarity_threshold):
            # Copy the relevant image to the new path
            with open(source_image_path, 'rb') as f_source, open(destination_image_path, 'wb') as f_destination:
                f_destination.write(f_source.read())
            print(f"Saved {image_name} to {destination_folder}.")

# Define the source and destination image folder paths
source_folder = '../data/image_files'
destination_folder = '../data/clarified_images'

# Save relevant images to the new path
save_relevant_images(source_folder, destination_folder)

# Print a success message
print("Relevant images have been saved to the new path based on clarity.")

Saved label_0_index_0.png to ../data/clarified_images.
Saved label_0_index_10001.png to ../data/clarified_images.
Saved label_0_index_10015.png to ../data/clarified_images.
Saved label_0_index_10036.png to ../data/clarified_images.
Saved label_0_index_10037.png to ../data/clarified_images.
Saved label_0_index_10051.png to ../data/clarified_images.
Saved label_0_index_10056.png to ../data/clarified_images.
Saved label_0_index_10062.png to ../data/clarified_images.
Saved label_0_index_10064.png to ../data/clarified_images.
Saved label_0_index_10068.png to ../data/clarified_images.
Saved label_0_index_10078.png to ../data/clarified_images.
Saved label_0_index_10094.png to ../data/clarified_images.
Saved label_0_index_10099.png to ../data/clarified_images.
Saved label_0_index_10104.png to ../data/clarified_images.
Saved label_0_index_10114.png to ../data/clarified_images.
Saved label_0_index_10120.png to ../data/clarified_images.
Saved label_0_index_10121.png to ../data/clarified_images.
S

### Group Data

In [ ]:
# load CSV file
data = pd.read_csv('../data/dataset.csv', skiprows=1)

# create destination directory
root_save_path = '../data/dataset/'
if not os.path.exists(root_save_path):
    os.makedirs(root_save_path)

# group images by lable
grouped = data.groupby(data.columns[0])

# extract and save data by in defferent directories
for label, group in grouped:
    label_save_path = os.path.join(root_save_path, str(label))
    if not os.path.exists(label_save_path):
        os.makedirs(label_save_path)
    csv_file_path = os.path.join(label_save_path, f'label_{label}.csv')
    group.to_csv(csv_file_path, header=False, index=False)


### Make Images Under Label

In [13]:
def load_data(filepath):
    """Load CSV data into a DataFrame."""
    return pd.read_csv(filepath)

for label in range(7):
    # load CSV data
    data = pd.read_csv(f'../data/dataset/{label}/label_{label}.csv', skiprows=1)

    save_path = f'../data/dataset/{label}/image_files'
    if not os.path.exists(save_path):
        os.makedirs(save_path)

    # read dataset.csv data {lable, pixcels}
    for index, row in data.iterrows():
        pixels = row.iloc[1].split(' ')
        pixels = list(map(int, pixels))
        
        # calculate image real sizes
        image_size = int(math.sqrt(len(pixels)))
        image_array = np.array(pixels, dtype=np.uint8).reshape((image_size, image_size))
        
        # creat image and save
        image = Image.fromarray(image_array)
        image.save(os.path.join(save_path, f'label_{label}_index_{index}.png'))

### Clarify Dataset Under Label

In [16]:
# Define a function to calculate the clarity of an image
def calculate_image_clarity(image_path):
    image = cv2.imread(image_path)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    fm = cv2.Laplacian(gray, cv2.CV_64F).var()
    return fm

# Define a function to check if an image is clear enough
def is_image_clear(image_path, clarity_threshold=100):
    clarity = calculate_image_clarity(image_path)
    return clarity > clarity_threshold

# Define a function to save relevant images to a new path
def save_relevant_images(source_folder, destination_folder, clarity_threshold=100):
    if not os.path.exists(destination_folder):
        os.makedirs(destination_folder)
    
    for image_name in os.listdir(source_folder):
        source_image_path = os.path.join(source_folder, image_name)
        destination_image_path = os.path.join(destination_folder, image_name)
        
        if is_image_clear(source_image_path, clarity_threshold):
            # Copy the relevant image to the new path
            with open(source_image_path, 'rb') as f_source, open(destination_image_path, 'wb') as f_destination:
                f_destination.write(f_source.read())
            print(f"Saved {image_name} to {destination_folder}.")

# Define the source and destination image folder paths
for label in range(7):
    source_folder = f'../data/dataset/{label}/image_files'
    destination_folder = f'../data/dataset/{label}/clarified_images'

    # Save relevant images to the new path
    save_relevant_images(source_folder, destination_folder)

# Print a success message
print("Relevant images have been saved to the new path based on clarity.")

Saved label_0_index_0.png to ../data/train/0/clarified_images.
Saved label_0_index_1.png to ../data/train/0/clarified_images.
Saved label_0_index_10.png to ../data/train/0/clarified_images.
Saved label_0_index_100.png to ../data/train/0/clarified_images.
Saved label_0_index_1000.png to ../data/train/0/clarified_images.
Saved label_0_index_1001.png to ../data/train/0/clarified_images.
Saved label_0_index_1002.png to ../data/train/0/clarified_images.
Saved label_0_index_1003.png to ../data/train/0/clarified_images.
Saved label_0_index_1004.png to ../data/train/0/clarified_images.
Saved label_0_index_1005.png to ../data/train/0/clarified_images.
Saved label_0_index_1006.png to ../data/train/0/clarified_images.
Saved label_0_index_1007.png to ../data/train/0/clarified_images.
Saved label_0_index_1008.png to ../data/train/0/clarified_images.
Saved label_0_index_1009.png to ../data/train/0/clarified_images.
Saved label_0_index_101.png to ../data/train/0/clarified_images.
Saved label_0_index_